## TP n°4: distance de Levenshtein  [Corrigé question 2]

La distance de Levenshtein, ou distance d'édition, est une façon de mesurer à quel point deux mots se ressemblent. L'idée de base est d'attribuer un poids à chacune des opérations qui peuvent permettre de passer d'un mot à un autre (suppression ou insertion d'une lettre, interversion de deux lettres, remplacement d'une lettre par une autre...).
La distance est calculée à partir de ce nombre d'opérations (éventuellement pondérées).
<br/>Cette notion est très utilisée pour faire de la correction orthographique, pour gérer les tokens inconnus dans de nombreuses applications de TAL, pour faire de la morphologie computationnelle, _etc_.
<br/>L'article Wikipedia https://fr.wikipedia.org/wiki/Distance_de_Levenshtein est une bonne source d'information. On y donne même une version de l'algorithme, mais je propose plutôt une approche progressive pour mieux appréhender les aspects algorithmiques du problème: on va implémenter différentes fonctions de mesure de distance qui en faisant différentes hypothèses simplificatrices.

### Prise en compte (simplifiée) des substitutions

1. Ecrire une fonction `nb_subst(u,v)` qui renvoie le nombre de substitutions d'un caractère qui distinguent u de v. Par hypothèse les deux chaînes sont de même longueur (sinon on renvoie -1), et la seule opération mesurée est le remplacement d'un caractère par un autre. 
2. Cette valeur dépend bien sûr du nombre de lettres du mot. On peut essayer de prendre cela en compte en renvoyant le ratio de caractères modifiés par rapport au nombre total de caractères: la distance maximale est alors à 1 (tous les caractères sont différents). Implémenter cette fonction `dist_subst(u,v)`.
3. Cette fonction est une fonction _partielle_ : elle ne permet pas de définir une distance entre deux chaînes quelconques, mais seulement entre deux chaînes de même longueur. Pour passer à une mesure totale, on peut proposer que si les deux chaînes ne sont pas de même longueur, on fait comme si on rallongeait artificiellement la plus courte en ajoutant des caractères toujours différents de leur correspondant dans la chaîne la plus longue. Le nombre d'opérations peut être interprété comme _le nombre de caractères à modifier ou à supprimer pour passer de la chaîne la plus longue à la plus courte_. Comme précédemment, on va renvoyer un ratio plutôt qu'un nombre brut. Implémenter cette fonction `subst_totale(u,v)`. 
4. Pour tester les fonctions : 
    1. Faites un jeu d'essai (paires de mots) qui correspondent aux différents cas de figure que vous pouvez anticiper.  Augmentez systématiquement ce jeu d'essai, en vérifiant bien sûr que vos prédictions sont correctes. 
    2. Prennez plusieurs centaines de mots-formes dans un texte (pas trop quand-même: 200 c'est bien) de la façon dont on a procédé dans les TP précédents, et calculez les distances 2 à 2: regardez quels sont les mots les plus proches (mais quand-même différents), etc. 
    
Une fois vos tests réalisés, vous constaterez que, sans surprise, les mots les plus proches (mais différents) sont les paires de mots les plus longs qui ne diffèrent que d'une seule lettre. En effet, à cause de la normalisation effectuée, une différence d'un seul caractère est comptée comme plus petite si le mot a plus de lettres. Cela peut correspondre à une certaine intuition, mais dans la pratique la distance proposée par Levenshtein ne procède pas à une normalisation. 

### Autre approche : prise en compte de séquences absentes

Ecrire une fonction qui va s'appliquer à deux chaînes de caractères telles que la seconde est obtenue à partie de la première en ôtant une (seule) portion *contiguë*. La fonction `coupe(u,v)` doit renvoyer la taille de la coupe qui a été pratiquée dans _u_ pour obtenir _v_. 
<br/>Formellement: $\exists a,b,w \mbox{ t.q. } u = awb \;\&\; v = ab$, où $a$, $b$ et $w$ sont des chaînes de caractères non vides. 
<br/>La fonction doit renvoyer -1 si la condition n'est pas vérifiée (0 signifie que u==v).

Indice algorithmique: il faut chercher d'une part le préfixe commun, d'autre part le suffixe commun: si ces deux sous-chaînes sont non vides, il ne reste plus qu'à compter la taille de $w$.

### Implémentation de la distance de Levenshtein standard

Les deux questions précédentes permettent de se faire une (petite) idée de la complexité de la version complète de l'algorithme. La troisième partie du TP va consister à implémenter l'algorithme, en partant de la version proposé dans la page wikipedia. C'est un algorithme de programmation dynamique: l'idée est de stocker le plus possible de résultats intermédiaires pour ne les faire qu'une seule fois. La base de l'algorithme est donc la table qui stocke ces informations. 

1. Essayer de faire tourner l'algo sur quelques exemples à la main pour comprendre son esprit général. Les exemples de la page peuvent aider. 
2. Adapter en python l'algorithme de la page. On trouve facilement sur internet des bouts de code qui implémentent l'algorithme, mais j'espère que vous avez compris le peu d'intérêt qu'il y a à recopier du code si on ne comprend pas ce qu'il fait. 
3. Installer (avec anaconda ou pip) le package python-levenshtein, ce qui va vous permettre de comparer votre version à l'implémentation fournie par cette bibliothèque. 

#### Autre approche : mesure de la longueur de la coupe

Pour faciliter la programmation, on va définir deux fonctions qui vont s'occuper de déterminer la longueur du préfixe et du suffixe commun entre les deux chaînes. 
L'hypothèse est que si on regarde le mot "dest" (le mot résultant de la coupe) on trouve dans ce mot un indice $k$ tel que `dest[:k]` est un préfixe de "orig" (le mot avant la coupe) et tel que `dest[k:]` est un suffixe de orig. 

Autrement dit: `orig = dest[:k] + w + dest[k:]` 

Remarque: Dans la définition donnée dans l'énoncé, on a exclu les cas où la coupe se fait au début du mot (alors $k = 0$) et ceux où la coupe se fait à la fin: $k = len(dest)$. 

Attention à des cas particuliers rares mais qui doivent être pris en compte: supposons que l'on fasse une coupe de `ni` dans le mot `nininini`. Cela donne `ninini` quel que soit l'endroit où l'on fait la coupe. Autrement dit, dans un tel cas, on ne peut pas savoir s'il faut analyser la coupe comme `nini /ni/ ni` ou comme `ninini /ni/`. Les cas de ce genre sont caractérisés par le fait que la fin du préfixe commun au mot initial et au mot découpé ne coïncide pas avec le début du suffixe commun. 

In [1]:
# g (gauche) = indice du premier caractère différent entre u et v 
#            = taille du préfixe commun
# d (droite) = indice du premier caractère différent en partant de la fin
# --> len(v) - (d+1) = taille du suffixe commun
def taille_prefixe(u,v):
    N = len(v)
    g = 0
    while g < N and u[g] == v[g]:
        g += 1
    return g

def taille_suffixe(u,v):
    N = len(v)
    delta = len(u) - len(v)
    d = N - 1
    while d >= 0 and v[d] == u[d+delta]: 
        d -= 1
    return N-(d+1)

In [2]:
# Jeu de données pour tester les deux fonctions 
# (le 2e mot ne doit pas être plus long que le premier)
paires = [('valapiche', 'valache'), ('toto', 'toto'), ('saxe', 'vax'), ('nininini', 'ninini'),
          ('apolice', 'police'), ('pouliche', 'poule'), ('poule','pou'), ('dans', 'des')]

for (x,y) in paires: 
    tp, ts = taille_prefixe(x,y), taille_suffixe(x,y)
    print("%-10s /%6s/ %-10s /%6s/ (%d,%d)"%
         (x,y[:tp],y,y[-ts:] if ts != 0 else '',tp,ts))

valapiche  /  vala/ valache    /   che/ (4,3)
toto       /  toto/ toto       /  toto/ (4,4)
saxe       /      / vax        /      / (0,0)
nininini   /ninini/ ninini     /ninini/ (6,6)
apolice    /      / police     /police/ (0,6)
pouliche   /  poul/ poule      /     e/ (4,1)
poule      /   pou/ pou        /      / (3,0)
dans       /     d/ des        /     s/ (1,1)


Une fois qu'on dispose de la taille des préfixes et suffixes communs (soient $p$ et $s$), on peut répondre à la question du TP. On ne considère que les cas où le préfixe et le suffixe sont tous deux non nuls : $p > 0$ et $s > 0$.
Dans ce cas il faut distinguer deux situations: 
1. le préfixe et le suffixe ne se chevauchent pas: $p + s \leq len(v)$. Alors:
  1. Soit $p + s < len(v)$. Dans ce cas, on ne peut pas dire que $v$ soit le résultat d'une coupe dans $u$: il y a des caractères dans $v$ qui ne viennent pas de $u$ (on a $u = awb$ et $v = aw'b$ avec $w' \not= \varepsilon$). Il faut renvoyer -1. 
  2. Soit $p + s = len(v)$, et on est exactement dans le cas où $u = awb$ et $v = ab$ avec $a$, $b$ et $w$ non nuls. La taille de la coupe est la différence de longueur entre $u$ et $v$. 
2. le préfixe et le suffixe se chevauchent : $p + s \geq len(v)$. Alors:
  1. Soit les deux mots $u$ et $v$ sont identiques (ainsi, par conséquent, que leurs préfixes et suffixes communs). Dans ce cas, la longueur de la coupe est 0 (ce qui correspond à la différence de longueurs).
  2. Soit les deux mots sont différents. Cela signifie que le préfixe commun a (au moins) un suffixe identique à un préfixe du suffixe commun [**Relisez cette phrase tranquillement en prenant des exemples...**]. Par exemple `u = "nininini"` et `v = "ninini"`, ou `u = "abcdbcde"` et `v = "abcde"`. Dans ce cas on ne peut pas donner la position de la coupe, mais on peut donner la taille: c'est $len(u) - len(v)$.

In [3]:
def coupe(u,v):
    p = taille_prefixe(u,v)
    s = taille_suffixe(u,v)
    if p > 0 and s > 0 and p+s >= len(v):
        return len(u) - len(v)
    else:
        return -1

In [4]:
for (x,y) in paires:
    c = coupe(x,y)
    if c > 0:
        print("%s a été coupé pour donner %s (taille de la coupe: %d)" % (x,y,c))

valapiche a été coupé pour donner valache (taille de la coupe: 2)
nininini a été coupé pour donner ninini (taille de la coupe: 2)
pouliche a été coupé pour donner poule (taille de la coupe: 3)


In [5]:
# Test avec des mots piochés dans un texte
def charge_fichier(nf):
    lgns = []
    with open(nf, "r", encoding="utf8") as f:
        for ligne in f:
            lgns.append(ligne.strip())
    return lgns
def charge_lexique(nf):
    liste_lignes = charge_fichier(nf)
    lexique = []
    for l in liste_lignes:
        for w in l.split():
            if w not in lexique:
                lexique.append(w)
    return lexique
formes = charge_lexique("pensees_pascal_utf8.txt")
formes = formes[200:500]
for i in range(len(formes)):
    for j in range(i,len(formes)):
        x,y = formes[i], formes[j]
        if len(x) < len(y):
            x,y = y,x
            c = coupe(x,y)
            if c > 0:
                print("%-15s : %-10s (%d)" % (x,y,c))

aperçu          : au         (4)
copies          : ces        (3)
choses          : ces        (3)
couvertes       : ces        (6)
perdu           : peu        (2)
combattraient   : combattent (3)
qu'elle         : quelle     (1)
mais            : mis        (1)
criassent       : crient     (3)
croient         : crient     (1)
faudrait        : fait       (4)
